In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

plt.style.use('ggplot')

import nltk

from transformers import AutoTokenizer
from transformers import TFAutoModelForSequenceClassification
from scipy.special import softmax
from time import sleep
from tqdm import tqdm, trange
from nltk.sentiment import SentimentIntensityAnalyzer
from tqdm import tqdm
import tensorflow as tf

2023-02-11 14:19:44.986397: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
df = pd.read_csv("./data/nltk_lyric_sentiment.csv")

In [3]:
df.drop(columns=["Unnamed: 0", 'neg', 'neu', 'pos', 'compound', 'lyrics_clean', 'text_tokenized'], axis=1, inplace=True)

In [4]:
df.shape

(26051, 11)

In [5]:
df2 = df.drop(df[df['num_lyrics'] > 100].index)

In [6]:
df2.shape

(405, 11)

In [7]:
df3 = df[0:10]

In [8]:
df3

song_id  chart_position  \
0                        "B" GirlsYoung And Restless              91   
1                             "Joy" Pt. IIsaac Hayes              72   
2                              #1 Dee JayGoody Goody              99   
3                                            #1Nelly              75   
4                                #9 DreamJohn Lennon              68   
5            #BeautifulMariah Carey Featuring Miguel              95   
6                            #SELFIEThe Chainsmokers              95   
7        #thatPOWERwill.i.am Featuring Justin Bieber              85   
8  $ave Dat MoneyLil Dicky Featuring Fetty Wap & ...             100   
9  '03 Bonnie & ClydeJay-Z Featuring Beyonce Knowles              56   

   chart_date                song  \
0  1990-08-11           "B" Girls   
1  1974-02-16         "Joy" Pt. I   
2  1978-12-16          #1 Dee Jay   
3  2002-03-02                  #1   
4  1975-03-08            #9 Dream   
5  2013-09-07          #Beautiful   
6  2014-05-24             #SELFIE   
7  2013-07-20          #thatPOWER   
8  2016-03-19      $ave Dat Money   
9  2003-03-29  '03 Bonnie & Clyde   

                                         performer  time_on_chart  \
0                               Young And Restless             15   
1                                      Isaac Hayes              9   
2                                      Goody Goody              5   
3                                            Nelly             20   
4                                      John Lennon             12   
5                    Mariah Carey Featuring Miguel             16   
6                                 The Chainsmokers             11   
7                will.i.am Featuring Justin Bieber             16   
8  Lil Dicky Featuring Fetty Wap & Rich Homie Quan             19   
9                  Jay-Z Featuring Beyonce Knowles             23   

   consecutive_weeks  worst_position chart_debut  \
0               14.0              91  1990-05-05   
1                8.0              72  1973-12-22   
2                4.0              99  1978-11-18   
3               19.0              75  2001-10-20   
4               11.0              68  1974-12-21   
5               15.0              95  2013-05-25   
6               10.0              95  2014-03-15   
7               15.0              85  2013-04-06   
8               12.0             100  2015-10-10   
9               22.0              56  2002-10-26   

                                              lyrics  num_lyrics  
0  “B” Girls LyricsIntro\nHey Slim Come here chec...         551  
1  1212 Songs LyricsAAlex Turner  Stuck on the Pu...         857  
2  Lbo3d l’akhar LyricsVerse 1 Omar Cravate\n\nBa...         577  
3  1 LyricsIntro\nUh uh uh\nI just gotta bring it...         723  
4  9 Dream LyricsVerse 1\nSo long ago\nWas it in ...         206  
5  Beautiful LyricsIntro Mariah Carey\nAh ah you’...         292  
6  TranslationsPortuguêsEnglishSELFIE LyricsVerse...         365  
7  TranslationsPortuguêsthatPOWER LyricsInstrumen...         435  
8  ave Dat Money LyricsIntro Lil Dicky  Fetty Wap...        1124  
9  ’03 Bonnie  Clyde LyricsIntro JAYZ\nUhh uhh uh...         622

In [9]:
sia = SentimentIntensityAnalyzer()

In [10]:
MODEL = f"cardiffnlp/twitter-roberta-base-sentiment"
tokenizer = AutoTokenizer.from_pretrained(MODEL)
model = TFAutoModelForSequenceClassification.from_pretrained(MODEL)

2023-02-11 14:20:07.781203: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
All model checkpoint layers were used when initializing TFRobertaForSequenceClassification.

All the layers of TFRobertaForSequenceClassification were initialized from the model checkpoint at cardiffnlp/twitter-roberta-base-sentiment.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFRobertaForSequenceClassification for predictions without further training.


In [11]:
def polarity_scores_roberta(example):
    encoded_text = tokenizer(example, return_tensors='tf')

    
   # def function(**encoded_text):
    #    for i in encoded_text:
     #       print(i, encoded_text[i])
    
    #function(**encoded_text)

    output = model(**encoded_text)
    scores = output[0][0].numpy()
    scores = softmax(scores)
    scores_dict = {
        'roberta_neg' : scores[0],
        'roberta_neu' : scores[1],
        'roberta_pos' : scores[2]
    }
    
    return scores_dict

In [12]:
res = {}
exceptions = {}

for i, row in tqdm(df.iterrows(), total=1):
    try:
        text = row['lyrics']
        Id = row['song_id']
        vader_result = sia.polarity_scores(text)
        vader_result_rename = {}
        for key, value in vader_result.items():
            vader_result_rename[f"vader_{key}"] = value
        #print(i)
        #print("--")
        roberta_result = polarity_scores_roberta(text)
        both = {**vader_result_rename, **roberta_result}
        res[Id] = both
        print(both)
    except:
        exceptions[Id] = Id

5it [00:02,  1.19it/s]                       

{'vader_neg': 0.012, 'vader_neu': 0.893, 'vader_pos': 0.095, 'vader_compound': 0.9124, 'roberta_neg': 0.07051061, 'roberta_neu': 0.69849896, 'roberta_pos': 0.2309904}


6it [00:05,  1.27s/it]

{'vader_neg': 0.063, 'vader_neu': 0.581, 'vader_pos': 0.356, 'vader_compound': 0.9988, 'roberta_neg': 0.27602938, 'roberta_neu': 0.36615252, 'roberta_pos': 0.3578182}


9it [00:07,  1.20it/s]

...

{'vader_neg': 0.02, 'vader_neu': 0.819, 'vader_pos': 0.161, 'vader_compound': 0.9144, 'roberta_neg': 0.18723278, 'roberta_neu': 0.65079206, 'roberta_pos': 0.1619752}


26050it [7:37:57,  1.32it/s]

{'vader_neg': 0.075, 'vader_neu': 0.758, 'vader_pos': 0.167, 'vader_compound': 0.9931, 'roberta_neg': 0.053149436, 'roberta_neu': 0.5273547, 'roberta_pos': 0.41949573}


26051it [7:37:59,  1.05s/it]

{'vader_neg': 0.062, 'vader_neu': 0.844, 'vader_pos': 0.093, 'vader_compound': 0.8176, 'roberta_neg': 0.040924188, 'roberta_neu': 0.52469987, 'roberta_pos': 0.43437594}


In [13]:
Result = pd.DataFrame(res).T
#sentiment_df = Result.merge(df, right_on = 'song_id')

In [14]:
Result.shape

(17373, 7)

In [15]:
Result

vader_neg  vader_neu  vader_pos  \
#9 DreamJohn Lennon                          0.012      0.893      0.095   
#BeautifulMariah Carey Featuring Miguel      0.063      0.581      0.356   
#SELFIEThe Chainsmokers                      0.105      0.804      0.092   
'65 Love AffairPaul Davis                    0.091      0.633      0.275   
'Til Summer Comes AroundKeith Urban          0.064      0.814      0.121   
...                                            ...        ...        ...   
ilysurf mesa Featuring Emilee                0.077      0.517      0.405   
sobeautifulMusiq Soulchild                   0.010      0.725      0.265   
whoa (mind in awe)XXXTENTACION               0.020      0.819      0.161   
whoknowsMusiq                                0.075      0.758      0.167   
www.memoryAlan Jackson                       0.062      0.844      0.093   

                                         vader_compound  roberta_neg  \
#9 DreamJohn Lennon                              0.9124     0.070511   
#BeautifulMariah Carey Featuring Miguel          0.9988     0.276029   
#SELFIEThe Chainsmokers                         -0.6048     0.555181   
'65 Love AffairPaul Davis                        0.9975     0.114197   
'Til Summer Comes AroundKeith Urban              0.9741     0.119455   
...                                                 ...          ...   
ilysurf mesa Featuring Emilee                    0.9987     0.015158   
sobeautifulMusiq Soulchild                       0.9985     0.014158   
whoa (mind in awe)XXXTENTACION                   0.9144     0.187233   
whoknowsMusiq                                    0.9931     0.053149   
www.memoryAlan Jackson                           0.8176     0.040924   

                                         roberta_neu  roberta_pos  
#9 DreamJohn Lennon                         0.698499     0.230990  
#BeautifulMariah Carey Featuring Miguel     0.366153     0.357818  
#SELFIEThe Chainsmokers                     0.385891     0.058927  
'65 Love AffairPaul Davis                   0.600194     0.285609  
'Til Summer Comes AroundKeith Urban         0.573680     0.306866  
...                                              ...          ...  
ilysurf mesa Featuring Emilee               0.285817     0.699025  
sobeautifulMusiq Soulchild                  0.155045     0.830797  
whoa (mind in awe)XXXTENTACION              0.650792     0.161975  
whoknowsMusiq                               0.527355     0.419496  
www.memoryAlan Jackson                      0.524700     0.434376  

[17373 rows x 7 columns]

In [20]:
Result.reset_index(inplace=True)

In [22]:
from pathlib import Path
filepath = Path("./data/sentiment_results.csv")

In [23]:
Result.to_csv(filepath)

In [16]:
len(exceptions)

8678

In [42]:
filepath2 = Path("./data/exceptions.csv")

In [24]:
type(exceptions)

dict

In [26]:
exceptions_df = pd.DataFrame.from_dict(exceptions, orient='index')

In [28]:
exceptions_df.reset_index(inplace = True)

In [38]:
exceptions_df.rename(columns={0:'song_id'}, inplace=True)

In [40]:
exceptions_df.drop(columns=['index'], axis=1, inplace=True)

In [43]:
exceptions_df.to_csv(filepath2)